### Conjugate gradient methods

This is an implementation of the conjugate gradient method on the discretised Poisson problem on a unit square. 

$$
  -u_{xx} - u_{yy} = f(x), \quad \text{on} \quad \Omega = (0,1)^2
$$
with $u=g^D$ at the boundary. See also Strikwerda, section 14.3

In [ ]:
%matplotlib inline
import numpy as np             
from scipy.linalg import solve    
import scipy.sparse as sparse             # Sparse matrices
from scipy.sparse.linalg import spsolve   # Linear solver for sparse matrices
import matplotlib.pyplot as plt
newparams = {'figure.figsize': (8.0, 4.0), 'axes.grid': True,
             'lines.markersize': 8, 'lines.linewidth': 2,
             
             'font.size': 14}
plt.rcParams.update(newparams)
from mpl_toolkits.mplot3d import Axes3D     # For 3-d plot
from matplotlib import cm

To test the implementation, use a problem with exact solution
$$
  u(x,y) = \cos(x)\sin(x)
$$

In [ ]:
# Source function
def f(x,y):
    return 2*np.cos(x)*np.sin(y)

# Dirichlet boundary conditions (and exact solution)
def gd(x,y):
    return np.cos(x)*np.sin(y)

The equation is discretized by the 5-point formula, giving
$$
   L(U_P) = 4U_P-U_W-U_E-U_S-U_N = h^2 f_p, \qquad \forall P\in \mathbb{G} \qquad \text{inner gridpoints}
$$
or 
$$ 
 L(U_{ij}) = 4U_{ij}-U_{i-1,j}-U_{i+1,j}-U_{i,j+1}-U_{i,j-1}=h^2f(x_i,j_i) 
$$
for $i,j=1,\dotsc,M-1$. 

The function below perform the operator $L(U)$ at all the inner gridpoint simultaneous. It returns 0 on all boundary gridpoints. 

In [ ]:
def L(U):
    X = np.zeros(np.shape(U))
    X[1:-1,1:-1] = 4*U[1:-1,1:-1]-U[:-2,1:-1]-U[2:,1:-1]-U[1:-1,2:]-U[1:-1,:-2]
    return X

Implementation of CG on the above problem. 
See Strikwerda, eq (14.2.7) for the general algorithm.
Following the idea there, the iterations terminates when the norm of the update is smaller than a tolerance
$$ h\alpha\|p\|_2 <tol. $$

In [ ]:
M = 10
tol = 1.e-7
h = 1/M
x = np.linspace(0,1,M+1)
y = np.linspace(0,1,M+1)
xx, yy = np.meshgrid(x,y)

# CG starts here
# Initialization
r = np.zeros((M+1,M+1))
p = np.zeros((M+1,M+1))
q = np.zeros((M+1,M+1))          # q=A*p

# Initial guess: U=0 in the inner points, and known at the boundaries. 
U = gd(xx,yy)        
U[1:-1,1:-1] = 0 

r[1:-1,1:-1] = h**2*f(xx[1:-1,1:-1],yy[1:-1,1:-1])     
r = r-L(U)                   # r = b-AU       
r2 = np.sum(r**2)            # ||r||^2                     
p[1:-1,1:-1]=r[1:-1,1:-1]    # p = r
q = L(p)                     # q = Ap
pq = np.sum(p*q)             # p^TAp=p^Tq

# start of iterations
for k in range((M-1)**2):
    alpha = r2/pq
    U = U+alpha*p
    error = h*alpha*np.sqrt(np.sum(p**2))
    if error <tol:
        break
    r = r-alpha*q
    r2_new = np.sum(r**2)
    beta = r2_new/r2
    p = r+beta*p
    q = L(p)
    r2 = r2_new
    pq = np.sum(p*q)
    print('k=',k, ', error=',error)
print('k=',k, ', error=',error)



In [ ]:
# Plot the solution
fig = plt.figure()
ax = fig.gca(projection='3d')
ax.plot_surface(xx, yy, U, cmap=cm.coolwarm)            # Surface-plot
#ax.plot_wireframe(X, Y, U)         # Mesh-plot
plt.xlabel('x')
plt.ylabel('y')
plt.title('The solution of Poisson equation');